In [1]:
import sys
sys.path.append("/veRL/veRL/cyk/vla-mix/verl")
sys.path.append("/file_system/cyk/vla_mix/LIBERO/")
import functools
import multiprocessing as mp

import numpy as np
import torch


original_torch_load = torch.load


# @functools.wraps(original_torch_load)
# def new_torch_load(*args, **kwargs):
#     if "weights_only" not in kwargs:
#         kwargs["weights_only"] = False
#     return original_torch_load(*args, **kwargs)


# torch.load = new_torch_load

In [2]:
import os
import torch
import numpy as np
import json
import torch
import numpy as np
import math
from PIL import Image
from io import BytesIO
from verl.models.openvla_oft.configuration_prismatic import OpenVLAConfig
from verl.models.openvla_oft.modeling_prismatic import OpenVLAForActionPrediction
from verl.models.openvla_oft.processing_prismatic import PrismaticImageProcessor, PrismaticProcessor
# from transformers import AutoConfig, AutoImageProcessor, AutoModelForVision2Seq, AutoProcessor


Using LIBERO constants:
  NUM_ACTIONS_CHUNK = 8
  ACTION_DIM = 7
  PROPRIO_DIM = 8
  ACTION_PROPRIO_NORMALIZATION_TYPE = NormalizationType.BOUNDS_Q99
If needed, manually set the correct constants in `prismatic/vla/constants.py`!


In [3]:
local_path = "/file_system/common-models/Haozhan72-kangsheng/Openvla-oft-SFT-libero10-trajall/"
INFER_DEVICE = "cuda:0"
processor = PrismaticProcessor.from_pretrained(local_path, trust_remote_code=True)
tokenizer=processor.tokenizer

# override model kwargs
actor_model_config = OpenVLAConfig.from_pretrained(local_path, trust_remote_code=True)

torch_dtype = torch.float32
actor_module = OpenVLAForActionPrediction.from_pretrained(
                                        pretrained_model_name_or_path=local_path,
                                        torch_dtype=torch_dtype,
                                        #attn_implementation="flash_attention_2",
                                        config=actor_model_config,              
                                        trust_remote_code=True,
                                    )
actor_module.vision_backbone.set_num_images_in_input(1)
dataset_statistics_path = os.path.join(local_path, "dataset_statistics.json")
if os.path.isfile(dataset_statistics_path):
    with open(dataset_statistics_path, "r") as f:
        norm_stats = json.load(f)
    actor_module.norm_stats = norm_stats
actor_module = actor_module.to(INFER_DEVICE)
actor_module.eval()

Using a slow image processor as `use_fast` is unset and a slow processor was saved with this model. `use_fast=True` will be the default behavior in v4.52, even if the model was saved with a slow processor. This will result in minor differences in outputs. You'll still be able to use a slow processor with `use_fast=False`.


The argument `trust_remote_code` is to be used with Auto classes. It has no effect here and is ignored.
PrismaticForConditionalGeneration has generative capabilities, as `prepare_inputs_for_generation` is explicitly defined. However, it doesn't directly inherit from `GenerationMixin`. From 👉v4.50👈 onwards, `PreTrainedModel` will NOT inherit from `GenerationMixin`, and this model will lose the ability to call `generate` and other related functions.
  - If you're using `trust_remote_code=True`, you can get rid of this warning by loading the model with an auto class. See https://huggingface.co/docs/transformers/en/model_doc/auto#auto-classes
  - If you are the owner of the model architecture code, please modify your model class such that it inherits from `GenerationMixin` (after `PreTrainedModel`, otherwise you'll get an exception).
  - If you are not the owner of the model architecture class, please contact the model code owner to update it.
OpenVLAForActionPrediction has generative capa

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

PrismaticForConditionalGeneration has generative capabilities, as `prepare_inputs_for_generation` is explicitly defined. However, it doesn't directly inherit from `GenerationMixin`. From 👉v4.50👈 onwards, `PreTrainedModel` will NOT inherit from `GenerationMixin`, and this model will lose the ability to call `generate` and other related functions.
  - If you're using `trust_remote_code=True`, you can get rid of this warning by loading the model with an auto class. See https://huggingface.co/docs/transformers/en/model_doc/auto#auto-classes
  - If you are the owner of the model architecture code, please modify your model class such that it inherits from `GenerationMixin` (after `PreTrainedModel`, otherwise you'll get an exception).
  - If you are not the owner of the model architecture class, please contact the model code owner to update it.
OpenVLAForActionPrediction has generative capabilities, as `prepare_inputs_for_generation` is explicitly defined. However, it doesn't directly inherit

OpenVLAForActionPrediction(
  (vision_backbone): PrismaticVisionBackbone(
    (featurizer): VisionTransformer(
      (patch_embed): PatchEmbed(
        (proj): Conv2d(3, 1024, kernel_size=(14, 14), stride=(14, 14))
        (norm): Identity()
      )
      (pos_drop): Dropout(p=0.0, inplace=False)
      (patch_drop): Identity()
      (norm_pre): Identity()
      (blocks): Sequential(
        (0): Block(
          (norm1): LayerNorm((1024,), eps=1e-06, elementwise_affine=True)
          (attn): Attention(
            (qkv): Linear(in_features=1024, out_features=3072, bias=True)
            (q_norm): Identity()
            (k_norm): Identity()
            (attn_drop): Dropout(p=0.0, inplace=False)
            (proj): Linear(in_features=1024, out_features=1024, bias=True)
            (proj_drop): Dropout(p=0.0, inplace=False)
          )
          (ls1): LayerScale()
          (drop_path1): Identity()
          (norm2): LayerNorm((1024,), eps=1e-06, elementwise_affine=True)
          (mlp)

In [21]:
from PIL import Image
import torchvision.transforms.functional as F
from torch.nn.utils.rnn import pad_sequence
def center_crop_image(image: Image.Image) -> Image.Image:

    crop_scale = 0.9
    orig_w, orig_h = image.size
    image_tensor = F.to_tensor(image)
    crop_h = int(orig_h * crop_scale)
    crop_w = int(orig_w * crop_scale)
    image_tensor = F.center_crop(image_tensor, (crop_h, crop_w))
    image_tensor = F.resize(image_tensor, (orig_h, orig_w))
    final_image = F.to_pil_image(image_tensor)
    
    final_image = final_image.convert("RGB")
    return final_image

def resize_image(img, resize_size):
    assert isinstance(resize_size, tuple), "resize_size must be a tuple"
    assert isinstance(img, np.ndarray), "img must be a numpy array"
    
    # Convert numpy array to PIL Image
    pil_img = Image.fromarray(img)
    
    # Encode as JPEG, as done in RLDS dataset builder
    buffer = BytesIO()
    pil_img.save(buffer, format='JPEG')
    buffer.seek(0)
    
    # Immediately decode back
    img = Image.open(buffer)
    
    img = img.resize(resize_size, Image.Resampling.LANCZOS)
    img = np.array(img)
    img = np.clip(np.round(img), 0, 255).astype(np.uint8)
    
    return img

# def process_input(inputs:list, task_descriptions:list, config):
    
#     batchdata = {"input_ids":[],"attention_mask":[],"pixel_values":[]}  
    
#     for i in range(len(inputs)):
#         input = inputs[i]
#         task_description = task_descriptions[i]
        
#         image = Image.fromarray(input["full_image"]).convert("RGB")
#         if config["center_crop"]:
#             image = center_crop_image(image)
#         prompt = f"In: What action should the robot take to {task_description.lower()}?\nOut:"
#         batch_feature  = processor(prompt, image)
        
#         if "wrist_image" in input.keys():
#             wrist_image = Image.fromarray(input["wrist_image"]).convert("RGB")
#             if config["center_crop"]:
#                 wrist_image = center_crop_image(wrist_image)
#             wrist_batch_feature = processor(prompt, wrist_image)
#             primary_pixel_values = batch_feature["pixel_values"]
#             batch_feature["pixel_values"] = torch.cat([primary_pixel_values] + [wrist_batch_feature["pixel_values"]], dim=1)
            
#         input_ids = batch_feature["input_ids"]
#         attention_mask = batch_feature["attention_mask"]
#         pixel_values = batch_feature["pixel_values"]
        
#         if not torch.all(input_ids[:, -1] == 29871):
#             input_ids = torch.cat(
#                 (input_ids, torch.unsqueeze(torch.Tensor([29871]).long(), dim=0).to(input_ids.device)), dim=1
#             )
#             attention_mask = torch.cat(
#                 (attention_mask, torch.unsqueeze(torch.Tensor([True]).bool(), dim=0).to(attention_mask.device)), dim=1
#             )
        
#         batchdata["input_ids"].append(input_ids)    
#         batchdata["attention_mask"].append(attention_mask)    
#         batchdata["pixel_values"].append(pixel_values)    
    
    
#     device = torch.device('cuda') 
    
#     batchdata["input_ids"] = [x.transpose(0, 1) for x in batchdata["input_ids"]]
#     batchdata["attention_mask"] = [x.transpose(0, 1) for x in batchdata["attention_mask"]]
#     batchdata["input_ids"] = pad_sequence(batchdata["input_ids"], batch_first=True, padding_value=processor.tokenizer.pad_token_id).squeeze(-1).to(device)
#     batchdata["attention_mask"] = pad_sequence(batchdata["attention_mask"], batch_first=True, padding_value=0).squeeze(-1).to(device)
    
#     padding_mask = batchdata["input_ids"].ne(processor.tokenizer.pad_token_id)
#     assert  torch.all(padding_mask==batchdata["attention_mask"].ne(0))
#     padding_mask = ~padding_mask
#     padding_mask = padding_mask.int() 
#     sorted_indices = torch.argsort(padding_mask, dim=1, descending=True, stable=True)
#     batchdata["input_ids"] = torch.gather(batchdata["input_ids"], 1, sorted_indices)
#     batchdata["attention_mask"] = torch.gather(batchdata["attention_mask"], 1, sorted_indices)
    
    
#     batchdata["pixel_values"] = torch.cat(batchdata["pixel_values"] , dim=0).to(device)
#     assert torch.all(batchdata["attention_mask"].ne(0) == batchdata["input_ids"].ne(processor.tokenizer.pad_token_id))

#     return batchdata
def process_input(venv_obs, config):
    
    batchdata = {"input_ids":[],"attention_mask":[],"pixel_values":[]}  
    
    task_descriptions = venv_obs["task_descriptions"]
    images_and_states = venv_obs["images_and_states"]
    for i in range(len(venv_obs["task_descriptions"])):
        task_description = task_descriptions[i]
        image = resize_image(images_and_states["full_image"][i].numpy(), (224, 224))
        image = Image.fromarray(image).convert("RGB")
        if config["center_crop"]:
            image = center_crop_image(image)
        prompt = f"In: What action should the robot take to {task_description.lower()}?\nOut:"
        batch_feature  = processor(prompt, image)
        
        # if "wrist_image" in venv_obs.keys():
        #     wrist_image = Image.fromarray(input["wrist_image"]).convert("RGB")
        #     if config["center_crop"]:
        #         wrist_image = center_crop_image(wrist_image)
        #     wrist_batch_feature = processor(prompt, wrist_image)
        #     primary_pixel_values = batch_feature["pixel_values"]
        #     batch_feature["pixel_values"] = torch.cat([primary_pixel_values] + [wrist_batch_feature["pixel_values"]], dim=1)
            
        input_ids = batch_feature["input_ids"]
        attention_mask = batch_feature["attention_mask"]
        pixel_values = batch_feature["pixel_values"]
        
        if not torch.all(input_ids[:, -1] == 29871):
            input_ids = torch.cat(
                (input_ids, torch.unsqueeze(torch.Tensor([29871]).long(), dim=0).to(input_ids.device)), dim=1
            )
            attention_mask = torch.cat(
                (attention_mask, torch.unsqueeze(torch.Tensor([True]).bool(), dim=0).to(attention_mask.device)), dim=1
            )
        
        batchdata["input_ids"].append(input_ids)    
        batchdata["attention_mask"].append(attention_mask)    
        batchdata["pixel_values"].append(pixel_values)    
    
    
    device = torch.device('cuda') 
    
    batchdata["input_ids"] = [x.transpose(0, 1) for x in batchdata["input_ids"]]
    batchdata["attention_mask"] = [x.transpose(0, 1) for x in batchdata["attention_mask"]]
    batchdata["input_ids"] = pad_sequence(batchdata["input_ids"], batch_first=True, padding_value=processor.tokenizer.pad_token_id).squeeze(-1).to(device)
    batchdata["attention_mask"] = pad_sequence(batchdata["attention_mask"], batch_first=True, padding_value=0).squeeze(-1).to(device)
    
    padding_mask = batchdata["input_ids"].ne(processor.tokenizer.pad_token_id)
    assert  torch.all(padding_mask==batchdata["attention_mask"].ne(0))
    padding_mask = ~padding_mask
    padding_mask = padding_mask.int() 
    sorted_indices = torch.argsort(padding_mask, dim=1, descending=True, stable=True)
    batchdata["input_ids"] = torch.gather(batchdata["input_ids"], 1, sorted_indices)
    batchdata["attention_mask"] = torch.gather(batchdata["attention_mask"], 1, sorted_indices)
    
    
    batchdata["pixel_values"] = torch.cat(batchdata["pixel_values"] , dim=0).to(device)
    assert torch.all(batchdata["attention_mask"].ne(0) == batchdata["input_ids"].ne(processor.tokenizer.pad_token_id))

    return batchdata

In [5]:
# DO_SAMPLE = True
DO_SAMPLE = False
TEMP = 1.6
# TEMP = 0.2
UNNORM_KEY = "libero_10"
UNNORM_KEY = f"{UNNORM_KEY}_no_noops"
MAX_PROMPT_LENGTH = 512
def pad_sequence_to_length(tensors, max_seq_len, pad_token_id, left_pad=False):
    """
    pad a 2D tensors (e.g. responses, logprobs) in the last dim to max_seq_length.
    input shape: [bs, seq_length]
    output shape: [bs, max_seq_length]
    (0, max_seq_len - tensors.shape[-1]) means right pad to max_seq_length and no left pad
    """
    if tensors.shape[-1] >= max_seq_len:
        return tensors
    pad_tuple = (max_seq_len - tensors.shape[-1], 0) if left_pad else (0, max_seq_len - tensors.shape[-1])
    return torch.nn.functional.pad(tensors, pad_tuple, 'constant', pad_token_id)

@torch.no_grad()
def _generate_one_step(prompts: dict):
    idx = prompts['input_ids']  # (bs, prompt_length)
    attention_mask = prompts['attention_mask']  # left-padded attention_mask
    pixel_values = prompts["pixel_values"]



    # make sampling args can be overriden by inputs
    do_sample = prompts.get('do_sample', DO_SAMPLE)


    temperature = prompts.get('temperature', TEMP)

    #generation_config = GenerationConfig(temperature=temperature, top_p=top_p, top_k=top_k)

    with torch.autocast(device_type='cuda', dtype=torch.bfloat16):
        actions, response = actor_module.generate_action_verl(
            input_ids=idx,
            pixel_values=pixel_values,
            attention_mask=attention_mask,
            padding_idx = processor.tokenizer.pad_token_id,
            do_sample=do_sample,
            unnorm_key=UNNORM_KEY,
            temperature=temperature,)
    
    
    assert processor.tokenizer.pad_token_id is not None

    assert idx.ndim == 2
    idx = pad_sequence_to_length(idx,max_seq_len=MAX_PROMPT_LENGTH,pad_token_id=processor.tokenizer.pad_token_id,left_pad=True)
    
    assert attention_mask.ndim == 2
    attention_mask = pad_sequence_to_length(attention_mask,max_seq_len=MAX_PROMPT_LENGTH,pad_token_id=0,left_pad=True)
    
    
    assert idx.device.type == 'cuda'
    assert response.device.type == 'cuda'
    #assert seq.device.type == 'cuda'
    assert attention_mask.device.type == 'cuda'
    assert pixel_values.device.type == 'cuda'
    batch ={
            'responses': response,
            'input_ids': idx,
            'attention_mask': attention_mask,
            "pixel_values":pixel_values,
            "action":actions,
        }

    return batch

In [66]:
from omegaconf import OmegaConf
if "libero_env" in globals():
    libero_env.env.close()
from verl.envs.libero.libero_env import LiberoEnv
batch_size = 16
cfg_dict = {
        "task_suite_name": "libero_10",
        # "task_suite_name": "libero_goal",
        "num_envs": batch_size,
        "group_size": 1,
        "num_group": batch_size,
        "seed": 0,
        # "use_fixed_reset_state_ids": False,
        "use_fixed_reset_state_ids": True,
        "ignore_terminations": False,
        "auto_reset": True,
        "max_episode_steps": 512,
        "use_rel_reward": False,
        "reward_coef": 1.0,
        "only_eval": True,
        "use_ordered_reset_state_ids": True,
        "num_images_in_input": 2,
        "init_params": {
            "camera_depths": False,
            "camera_heights": 256,
            "camera_widths": 256,
            "camera_names": ["agentview", "robot0_eye_in_hand"],
        },
        "controller_configs": {
            "type": "OSC_POSE",
            "input_max": 1,
            "input_min": -1,
            "output_max": [0.05, 0.05, 0.05, 0.5, 0.5, 0.5],
            "output_min": [-0.05, -0.05, -0.05, -0.5, -0.5, -0.5],
            "kp": 150,
            "damping_ratio": 1,
            "impedance_mode": "fixed",
            "kp_limits": [0, 300],
            "damping_ratio_limits": [0, 10],
            "position_limits": None,
            "orientation_limits": None,
            "uncouple_pos_ori": True,
            "control_delta": True,
            "interpolation": None,
            "ramp_ratio": 0.2,
        },
        "video_cfg": {
            "save_video": True,
            "video_base_dir": "/tmp/videos",
        },
    }
cfg = OmegaConf.create(cfg_dict)

In [27]:
obs_venv['images_and_states']['full_image'].shape

torch.Size([16, 256, 256, 3])

In [67]:
from collections import defaultdict
import copy
import torch.cuda.profiler as profiler
from tqdm import trange



# batch_size = 32
# batch_size = 8
# max_steps = 200
max_steps = 512
# max_steps = 1024
# max_steps = 256
action_chunks_len = 8
libero_env = LiberoEnv(cfg, rank=0, world_size=1)
libero_env.is_start = True
# The first call to step with actions=None will reset the environment
obs_venv, _, terminated_venv, truncated_venv, info_venv = libero_env.step(actions=None)
print("Initial data:", obs_venv)
# print("Initial data:", init_data)
# task_descriptions = [init_data['task_description']]
# print(f"Task description: {task_descriptions}")

# valid_video[init_data['task_file_name']].extend(init_data['valid_images'])
# env_data = copy.deepcopy(init_data)
# env_obs = env_data['obs']
# for step in trange(max_steps // action_chunks_len):
#     # print("Step:", step)
#     # prof.step()
#     inputs = [_obs_to_input(env_obs)]
#     vla_input = process_input(inputs, task_descriptions, config)
#     # vla_input.update(meta_info)
#     vla_output = _generate_one_step(vla_input)
#     actions = vla_output["action"]
#     step_data = {
#         "responses": vla_output["responses"],
#         "input_ids": vla_output["input_ids"],
#         "attention_mask": vla_output["attention_mask"],
#         "pixel_values": vla_output["pixel_values"],
#         "action": actions,
#         "step": step
#     }
#     vla_history.append(step_data)
    

#     result = libero_env.step(actions[0])
#     valid_video[init_data['task_file_name']].extend(result['valid_images'])
#     env_obs = result["obs"]

#     step += action_chunks_len
#     complete = result["complete"]
#     if complete:
#         print(f"Task completed at step {step}.")
#         break
    

[info] using task orders [0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
get task and trial id [ 50 100 150 200 250 300 350 400 450 500] [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15] [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0] [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15]


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

get task and trial id [ 50 100 150 200 250 300 350 400 450 500] [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15] [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0] [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15]
Initial data: {'images_and_states': {'full_image': tensor([[[[ 13,  13,  13],
          [ 13,  13,  13],
          [ 13,  13,  13],
          ...,
          [118, 116, 112],
          [118, 116, 112],
          [116, 114, 110]],

         [[ 13,  13,  13],
          [ 13,  13,  13],
          [ 13,  13,  13],
          ...,
          [118, 116, 112],
          [118, 116, 112],
          [116, 114, 110]],

         [[ 13,  13,  13],
          [ 13,  13,  13],
          [ 13,  13,  13],
          ...,
          [118, 116, 113],
          [118, 116, 112],
          [117, 115, 111]],

         ...,

         [[ 89,  62,  50],
          [ 88,  62,  49],
          [ 85,  61,  47],
          ...,
          [ 74,  53,  42],
          [ 72,  52,  42],
          [ 72,  52,  41]],



In [ ]:
# obs_venv
from verl.envs.libero.utils import normalize_gripper_action, invert_gripper_action
import rich
task_descriptions = obs_venv['task_descriptions']
rich.print(f"Task description: {task_descriptions}")
config = {
    "center_crop": True,
    "num_steps_wait": 10
}
vla_history = []
rollout_buffer = defaultdict(list)

In [79]:
for step in trange(max_steps // action_chunks_len):

    # print("Step:", step)
    # prof.step()
    vla_input = process_input(obs_venv, config)
    # vla_input.update(meta_info)
    vla_output = _generate_one_step(vla_input)
    actions = vla_output["action"]
    # if step < 1:
    #     actions = torch.tensor([[0, 0, 0, 0, 0, 0, 1]]).repeat(batch_size, action_chunks_len, 1).numpy()
    #     print(actions.shape)    
    # step_data = {
    #     "responses": vla_output["responses"],
    #     "input_ids": vla_output["input_ids"],
    #     "attention_mask": vla_output["attention_mask"],
    #     "pixel_values": vla_output["pixel_values"],
    #     "action": actions,
    #     "step": step
    # }
    # vla_history.append(step_data)
    rollout_buffer["input_ids"].append(vla_input["input_ids"].cpu())
    rollout_buffer["attention_mask"].append(vla_input["attention_mask"].cpu())
    rollout_buffer["pixel_values"].append(vla_input["pixel_values"].cpu())
    rollout_buffer["actions"].append(torch.tensor(actions))
    env_info_list = {}


    # TODO(caiyunke.astra): check if need to invert the gripper action
    # Invert the gripper action
    normalized_action = normalize_gripper_action(actions, binarize=True)
    inverted_action = invert_gripper_action(normalized_action)

    # actions[..., -1] = actions[..., -1] *  -1.0
    

    # result = libero_env.step(actions[0])
    # result = libero_env.chunk_step(actions)
    result = libero_env.chunk_step(inverted_action)
    obs_venv, chunk_rewards, chunk_terminations, chunk_truncations, infos = result
    chunk_dones = torch.logical_or(chunk_terminations, chunk_truncations)
    step += action_chunks_len
    # rollout_buffer["chunk_terminations"].append(chunk_terminations.cpu())
    # rollout_buffer["chunk_truncations"].append(chunk_truncations.cpu())
    if chunk_dones.any():
        if "final_info" in infos:
            final_info_mask = infos["_final_info"]
            final_info = infos["final_info"]
            done_mask = chunk_dones[:, -1]
            done_info = {
                "env_id": torch.tensor(final_info["env_id"])[done_mask].cpu(),
            }
            done_info.update({k :v[done_mask].cpu() for k, v in final_info['episode'].items()})
            for k, v in done_info.items():
                rollout_buffer[f"env_info/{k}"].append(v)


  8%|▊         | 5/64 [00:13<02:36,  2.65s/it]

get task and trial id [ 50 100 150 200 250 300 350 400 450 500] [10] [0] [10]


 11%|█         | 7/64 [00:20<02:56,  3.10s/it]

get task and trial id [ 50 100 150 200 250 300 350 400 450 500] [12] [0] [12]


 12%|█▎        | 8/64 [00:24<03:13,  3.46s/it]

...

 61%|██████    | 39/64 [01:58<01:14,  2.96s/it]

get task and trial id [ 50 100 150 200 250 300 350 400 450 500] [10] [0] [10]


 86%|████████▌ | 55/64 [02:45<00:25,  2.83s/it]

get task and trial id [ 50 100 150 200 250 300 350 400 450 500] [15] [0] [15]


100%|██████████| 64/64 [03:12<00:00,  3.01s/it]


In [80]:
rollout_buffer

defaultdict(list,
            {'input_ids': [tensor([[    1,   512, 29901,  1724,  3158,   881,   278, 19964,  2125,   304,
                        1925,  1716,   278, 22968, 22300,   322,   278,  6454,  1219, 12507,
                         346,   297,   278, 25972, 29973,    13,  3744, 29901, 29871],
                      [    1,   512, 29901,  1724,  3158,   881,   278, 19964,  2125,   304,
                        1925,  1716,   278, 22968, 22300,   322,   278,  6454,  1219, 12507,
                         346,   297,   278, 25972, 29973,    13,  3744, 29901, 29871],
                      [    1,   512, 29901,  1724,  3158,   881,   278, 19964,  2125,   304,
                        1925,  1716,   278, 22968, 22300,   322,   278,  6454,  1219, 12507,
                         346,   297,   278, 25972, 29973,    13,  3744, 29901, 29871],
                      [    1,   512, 29901,  1724,  3158,   881,   278, 19964,  2125,   304,
                        1925,  1716,   278, 22968, 22300,

In [73]:
final_info

{'env_id': [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15],
 'episode': {'success_once': tensor([False, False, False, False, False, False, False,  True, False, False,
          False, False, False, False, False, False]),
  'return': tensor([0., 0., 0., 0., 0., 0., 0., 4., 0., 0., 0., 0., 0., 0., 0., 0.]),
  'episode_len': tensor([240, 240, 240, 240, 240, 240, 240, 240, 240, 240, 240, 240, 240, 240,
          240, 240], dtype=torch.int32),
  'reward': tensor([0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0167, 0.0000,
          0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000])}}

In [ ]:
infos["final_info"]

{'env_id': [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15],
 'episode': {'success_once': tensor([False, False, False, False, False, False, False, False, False, False,
          False, False, False, False, False, False]),
  'return': tensor([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.]),
  'episode_len': tensor([512, 512, 512, 512, 512, 512, 200,  24, 512, 512, 224, 160, 208, 512,
          512,  88], dtype=torch.int32),
  'reward': tensor([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.])}}

In [81]:
rollout_buffer[f"env_info/reward"]

[tensor([0.0167]),
 tensor([0.0035]),
 tensor([0.0197]),
 tensor([0.0256]),
 tensor([0.0057]),
 tensor([0.0189]),
 tensor([0.0040]),
 tensor([0., 0., 0., 0., 0., 0., 0., 0., 0., 0.]),
 tensor([0.0257]),
 tensor([0.0038])]

In [82]:
final_rollout_batch = {}
for key, value_list in rollout_buffer.items():
    if not value_list:
        continue
        
    if "env_info/" in key:
        final_rollout_batch[key] = torch.cat(value_list, dim=0)
    else:
        final_rollout_batch[key] = torch.stack(value_list, dim=0)
if "env_info/success" in final_rollout_batch:
    total_successes = final_rollout_batch["env_info/success"].int().sum().item()
    total_episodes_finished = len(final_rollout_batch["env_info/success"])
    
    if total_episodes_finished > 0:
        success_rate = total_successes / total_episodes_finished
        print(f"\nEvaluation Finished:")
        print(f"  - Total episodes completed: {total_episodes_finished}")
        print(f"  - Total successes: {total_successes}")
        print(f"  - Success Rate: {success_rate:.2%} ({total_successes} / {total_episodes_finished})")
    else:
        print("\nEvaluation Finished: No episodes were completed during the evaluation.")
else:
        print("\nEvaluation Finished: 'env_info/success' key not found in collected data. Cannot compute success rate.")
print("\nCollected data shapes (T, B, ...):")
for key, value in final_rollout_batch.items():
    if "env_info/" not in key:
        print(f"  - {key}: {value.shape}")
print("\nCollected env_info shapes (N_finished, ...):")
for key, value in final_rollout_batch.items():
    if "env_info/" in key:
        print(f"  - {key}: {value.shape}")


Evaluation Finished: 'env_info/success' key not found in collected data. Cannot compute success rate.

Collected data shapes (T, B, ...):
  - input_ids: torch.Size([94, 16, 29])
  - attention_mask: torch.Size([94, 16, 29])
  - pixel_values: torch.Size([94, 16, 6, 224, 224])
  - actions: torch.Size([94, 16, 8, 7])

Collected env_info shapes (N_finished, ...):
  - env_info/env_id: torch.Size([19])
  - env_info/success_once: torch.Size([19])
  - env_info/return: torch.Size([19])
  - env_info/episode_len: torch.Size([19])
  - env_info/reward: torch.Size([19])


In [ ]:
final_rollout_batch["env_info/success_once"]
print(f"Success rate: {final_rollout_batch['env_info/success_once'].sum().item()} / {len(final_rollout_batch['env_info/success_once'])}")

SyntaxError: f-string: invalid syntax. Perhaps you forgot a comma? (1721993815.py, line 2)

In [ ]:
# libero_env.flush_video(video_sub_dir=f"episode_{7}")
libero_env.flush_video(video_sub_dir=f"test6")


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [ ]:
# libero_env.env.close()